In [1]:
import pandas as pd

## Summary

We explored our downloaded images in `EDA-DL-0-3.ipynb`, and established the following causes of duplication along with remedies:
1. The "patch" record (record 3477891) which required alignment in `Data-gen-1-1.ipynb`, resulting in `../metadata/Jiggins_Zenodo_Img_Master_3477891Patch.csv` used for download, is a duplication of all listed records. Additionally, it introduced extra copies of 4 images with incorrect labels for their views (i.e., dorsal vs ventral).
 - Solution: This record will be removed.
2. The remaining duplication (430 images x2) comes from 5 records: [4291095](https://zenodo.org/records/4291095), [2813153](https://zenodo.org/records/2813153), [5526257](https://zenodo.org/records/5526257), [2553977](https://zenodo.org/records/2553977), and [2552371](https://zenodo.org/records/2552371).
  - Though there is nothing in their descriptions on Zenodo to indicate this overlap occurred, record 4291095 duplicated 415 images from record 2813153. 104 of these images had their view/side labels (dorsal vs ventral) updated to reflect an earlier mislabeling in record 2813153; these were all RAW copies of the images. All other metadata was consistent across records.
  - Solution: Copies of these images and their metadata will be retained from the newer record, record 4291095.
  - Record 5526257 has 10 images that were added twice. All their metadata is consistent, so we will just keep the first instance of each image.
  - Records 2553977 and 2552371 are both "Miscellaneous Heliconius wing photographs (2001-2019)" Parts 3 & 1, respectively. Record 2553977 has duplicated images with matching metadata, though 3 of the 4 images have different filenames (`Image_name`). It seems to have resulted from typos or not indicating `cut`, as they are all close-up crops of a single wing. From this perspective, the view labels (dorsal) don't seem appropriate when we have more fine-grained indicators such as "forewing dorsal".
    - Suggestion that the entries in this record with `cut` in the filename not be used for general classification unless this variety is desired. These also appear to be all the `tif` images, which are often ignored.
    - Record 2552371 has one image duplicated with two different `CAMID`s assigned (different views as well). These will both be removed as the image has no indicator of the specimen ID in it. Note that these also were labeled `Heliconius sp.`.
3. Looking at images that were not duplicates, there are clearly still multiple images of the same specimen from the same perspective (eg., two dorsal images) that are also of the same file type (eg., both jpgs). Duplication was checked at the pixel level, so there is no guarantee that they are truly different images, but due to the scope of this collection (over 20 years), it does not seem unlikely that multiple images could have been taken of the same specimen. 
  - Suggestion/Solution: When determining splits using this data, follow these steps:
    1. Ensure you are looking at only **_one_** view (eg., dorsal or ventral).
    2. Ensure you are only looking one file type (`raw`, `jpg`, or `tif`).
    3. Reduce to only unique `CAMID`s.
    4. Generate splits as desired.
    5. Add images to splits based on matched `CAMID`s if multiple views are desired (i.e., if a `CAMID` is present in the dorsal training, add the matching ventral image to the training set).
    6. Be sure to check only desired categories are included, such as excluding hybrids or cross types, or specimens not labeled to the level of classification.


## Generate "Clean" Master Metadata File

We'll now generate a cleaned master metadata file from `../metadata/deduplication/Jiggins_Zenodo_Img_Master_3477891Patch_downloaded.csv` (generated in `EDA-DL-0-3.ipynb` from our download master file and checksums of successful downloads) following the solutions outlined above. 

In [2]:
STATS_COLS = ["X",
              "CAMID",
              "Image_name",
              "md5",
              "record_number",
              "Taxonomic_Name",
              "species",
              "subspecies",
              "genus",
              "Cross_Type",
              "View",
              "Locality",
              "Sex",
              "Dataset",
              "file_type"]

In [3]:
df = pd.read_csv("../metadata/deduplication/Jiggins_Zenodo_Img_Master_3477891Patch_downloaded.csv", low_memory = False)
df[STATS_COLS].info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 42143 entries, 0 to 42142
Data columns (total 15 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   X               42143 non-null  int64 
 1   CAMID           42143 non-null  object
 2   Image_name      42143 non-null  object
 3   md5             42143 non-null  object
 4   record_number   42143 non-null  int64 
 5   Taxonomic_Name  42143 non-null  object
 6   species         42143 non-null  object
 7   subspecies      24502 non-null  object
 8   genus           42143 non-null  object
 9   Cross_Type      4447 non-null   object
 10  View            41364 non-null  object
 11  Locality        29047 non-null  object
 12  Sex             33254 non-null  object
 13  Dataset         34924 non-null  object
 14  file_type       42143 non-null  object
dtypes: int64(2), object(13)
memory usage: 4.8+ MB


In [4]:
df[STATS_COLS].nunique()

X                 42143
CAMID             11968
Image_name        36216
md5               36212
record_number        30
Taxonomic_Name      366
species             246
subspecies          155
genus                94
Cross_Type           30
View                  7
Locality            644
Sex                   3
Dataset               7
file_type             3
dtype: int64

Observations:
- Half of the Zenodo records wind up with duplicated images. 
- `Image_name` uniqueness is close to `md5`, but there are 4 more unique image names than unique images. I believe this was from the duplication in reocrd 2553977. We can check when cleaning it. 
- None of the cross types are duplicated.
- We do have multiple unique images for a single `CAMID`, more than just dorsal vs ventral since there are 11968 unique CAMIDs and 36212 unique `md5` values (36212 = **3**x11968 + 308)

### Remove Record 3477891

This is just a duplication of images and we already have from earlier records, along with some extra duplication that gets mislabeled.

In [5]:
df_reduced = df.loc[df["record_number"] != 3477891].copy()
df_reduced[STATS_COLS].nunique()

X                 36642
CAMID             11968
Image_name        36216
md5               36212
record_number        29
Taxonomic_Name      366
species             246
subspecies          155
genus                94
Cross_Type           30
View                  7
Locality            644
Sex                   3
Dataset               7
file_type             3
dtype: int64

The only change is in `X` (our total entry count) and in `record_number` (expected since we removed one).

## Address Remaining Duplicates

The remaining duplicates are across 5 records and will require a bit more care to reslove (following the plan outlined at the top of the notebook and in the README).

### Record 4291095 & 2813153 Duplicates

There are 415 duplicates across these two records, with `View` corrections in record 4291095, so we will remove the duplicates from record 2813153.

In [6]:
df_reduced.columns

Index(['CAMID', 'X', 'Image_name', 'View', 'zenodo_name', 'zenodo_link',
       'Sequence', 'Taxonomic_Name', 'Locality', 'Sample_accession',
       'Collected_by', 'Other_ID', 'Date', 'Dataset', 'Store', 'Brood',
       'Death_Date', 'Cross_Type', 'Stage', 'Sex', 'Unit_Type', 'file_type',
       'record_number', 'species', 'subspecies', 'genus', 'file_url',
       'hybrid_stat', 'filename', 'filepath', 'md5'],
      dtype='object')

We start by marking all duplicate images since the decision of which to keep is dependent on comparisons between them.

In [7]:
df_reduced["md5_duplicated"] = df_reduced.duplicated("md5", keep = False)
df_reduced["md5_duplicated"].value_counts()

md5_duplicated
False    35782
True       860
Name: count, dtype: int64

In [8]:
duplicates = df_reduced[df_reduced["md5_duplicated"]]
dupes_2813153 = duplicates.loc[duplicates["record_number"] == 2813153]
#print(duplicates.loc[duplicates["record_number"] == 4291095])
dupes_2813153.shape[0]

415

We will record the `X` value from these 415 entries to remove them from the overall dataset in favor of the updated entries from record 4291095.

In [9]:
X_dupes_2813153 = list(dupes_2813153.X)

In [10]:
df_reduced_2 = df_reduced.loc[~df_reduced["X"].isin(X_dupes_2813153)]
df_reduced_2[STATS_COLS].nunique()

X                 36227
CAMID             11968
Image_name        36216
md5               36212
record_number        29
Taxonomic_Name      366
species             246
subspecies          155
genus                94
Cross_Type           30
View                  7
Locality            644
Sex                   3
Dataset               7
file_type             3
dtype: int64

As expected, our numbers are holding steady with a reduction in `X` values of 415.

### Record 5526257 Duplicates

For record 5526257, the 10 duplicated entries are all the same, so we will just check `.duplicated` and keep the first instance of each.

In [11]:
dupes_5526257 = duplicates.loc[duplicates["record_number"] == 5526257].copy()
dupes_5526257["dupe_entries"] = dupes_5526257.duplicated(["CAMID", "Image_name", "View", "Taxonomic_Name", "Locality", "md5"], keep = "first")
print(dupes_5526257["dupe_entries"].value_counts())

X_dupes_5526257 = list(dupes_5526257.loc[dupes_5526257["dupe_entries"], "X"])
len(X_dupes_5526257)

dupe_entries
False    10
True     10
Name: count, dtype: int64


10

In [12]:
df_reduced_3 = df_reduced_2.loc[~df_reduced_2["X"].isin(X_dupes_5526257)]
df_reduced_3[STATS_COLS].nunique()

X                 36217
CAMID             11968
Image_name        36216
md5               36212
record_number        29
Taxonomic_Name      366
species             246
subspecies          155
genus                94
Cross_Type           30
View                  7
Locality            644
Sex                   3
Dataset               7
file_type             3
dtype: int64

Reduction in `X` by 10, consistency in all other numbers.

### Record 2552371 Duplicates

We are removing both duplicates from this record as their metadata is contradictory and cannot be verified. (Two different CAMIDs, different filenames, different views, etc.)

In [13]:
dupes_2552371 = duplicates.loc[duplicates["record_number"] == 2552371]
X_dupes_2552371 = list(dupes_2552371["X"])
dupes_2552371

CAMID      X  Image_name     View  \
11978  CAM010354  23471  10354d.jpg   dorsal   
12010  CAM010362  23484  10362v.jpg  ventral   

                                          zenodo_name  \
11978  Heliconius_wing_old_photos_2001_2019_part1.csv   
12010  Heliconius_wing_old_photos_2001_2019_part1.csv   

                             zenodo_link Sequence  Taxonomic_Name Locality  \
11978  https://zenodo.org/record/2552371   10,354  Heliconius sp.      NaN   
12010  https://zenodo.org/record/2552371   10,362  Heliconius sp.      NaN   

      Sample_accession  ... record_number         species subspecies  \
11978              NaN  ...       2552371  Heliconius sp.        NaN   
12010              NaN  ...       2552371  Heliconius sp.        NaN   

            genus                                           file_url  \
11978  Heliconius  https://zenodo.org/record/2552371/files/10354d...   
12010  Heliconius  https://zenodo.org/record/2552371/files/10362v...   

      hybrid_stat          filename                                filepath  \
11978         NaN  23471_10354d.jpg  images/Heliconius sp./23471_10354d.jpg   
12010         NaN  23484_10362v.jpg  images/Heliconius sp./23484_10362v.jpg   

                                    md5 md5_duplicated  
11978  84d4ac6527458786cdb33166cd80e0a8           True  
12010  84d4ac6527458786cdb33166cd80e0a8           True  

[2 rows x 32 columns]

In [14]:
df_reduced_4 = df_reduced_3.loc[~df_reduced_3["X"].isin(X_dupes_2552371)]
df_reduced_4[STATS_COLS].nunique()

X                 36215
CAMID             11968
Image_name        36214
md5               36211
record_number        29
Taxonomic_Name      366
species             246
subspecies          155
genus                94
Cross_Type           30
View                  7
Locality            644
Sex                   3
Dataset               7
file_type             3
dtype: int64

Removing these two has reduced our `X` count by 2, as well as our number of unique `Image_name`s, and it reduced our unique image count (`md5`) by 1. Observe that our unique `CAMID` count has remained constant, so both specimens indicated by these duplicate images are still represented in the dataset.

### Record 2553977 Duplicates

The duplicated entries for record 2553977 are the most complicated in that their metadata is nearly exact, though a few have different filenames (`Image_name`) and we would like to preserve the version that has `_cut` in the name.

In [15]:
dupes_2553977 = duplicates.loc[duplicates["record_number"] == 2553977]
dupes_2553977[STATS_COLS].sort_values("md5")

X      CAMID                               Image_name  \
40141  26197  CAM050147      CAM050147_DS1_HW_IMG_8537_cut_3.tif   
40144  26196  CAM050147      CAM050147_DS1_HW_IMG_8537_cut_3.tif   
40112  26102  CAM050036      CAM050036_S1_9_FW_IMG_8547_wb_2.tif   
40116  26115  CAM050036     CAM050036_S1_9_FW_IMG_8547_cut_2.tif   
40138  26112  CAM050147             CAM050147_DS1_IMG_8513_4.tif   
40145  26117  CAM050147      CAM050147_DS1_FW_IMG_8513_cut_4.tif   
40113  26105  CAM050036   CAM050036_S1_9_HW_wt_IMG_8541_cut3.tif   
40120  26116  CAM050036  CAM050036_S1_9_HW_wt_IMG_8541_cut_3.tif   

                                    md5  record_number  \
40141  21e726df7076f5c13fe1441126bac4d5        2553977   
40144  21e726df7076f5c13fe1441126bac4d5        2553977   
40112  34adbd5596f977834fb2c6876d2f4493        2553977   
40116  34adbd5596f977834fb2c6876d2f4493        2553977   
40138  464801449aa127933d9619cb4e6f0a01        2553977   
40145  464801449aa127933d9619cb4e6f0a01        2553977   
40113  6d63d659fbc02369010938bbc229ad4d        2553977   
40120  6d63d659fbc02369010938bbc229ad4d        2553977   

                  Taxonomic_Name          species subspecies       genus  \
40141  Heliconius sara ssp. sara  Heliconius sara       sara  Heliconius   
40144  Heliconius sara ssp. sara  Heliconius sara       sara  Heliconius   
40112  Heliconius sara ssp. sara  Heliconius sara       sara  Heliconius   
40116  Heliconius sara ssp. sara  Heliconius sara       sara  Heliconius   
40138  Heliconius sara ssp. sara  Heliconius sara       sara  Heliconius   
40145  Heliconius sara ssp. sara  Heliconius sara       sara  Heliconius   
40113  Heliconius sara ssp. sara  Heliconius sara       sara  Heliconius   
40120  Heliconius sara ssp. sara  Heliconius sara       sara  Heliconius   

      Cross_Type    View            Locality  Sex Dataset file_type  
40141        NaN  dorsal           Madingley  NaN     NaN       tif  
40144        NaN  dorsal           Madingley  NaN     NaN       tif  
40112        NaN  dorsal  Gamboa_insectaries  NaN     NaN       tif  
40116        NaN  dorsal  Gamboa_insectaries  NaN     NaN       tif  
40138        NaN  dorsal           Madingley  NaN     NaN       tif  
40145        NaN  dorsal           Madingley  NaN     NaN       tif  
40113        NaN  dorsal  Gamboa_insectaries  NaN     NaN       tif  
40120        NaN  dorsal  Gamboa_insectaries  NaN     NaN       tif

For each of these, we want the one with `_cut_` in the `Image_name`.

In [16]:
X_dupes_2553977 = [x for x in list(dupes_2553977["X"]) if "_cut_" not in dupes_2553977.loc[dupes_2553977["X"] == x, "Image_name"].values[0]]

# Check we got the ones expected
X_dupes_2553977

[26102, 26105, 26112]

In [17]:
# Add 26196, since both those entries (26196 and 26197) are the same
X_dupes_2553977.append(26196)


In [18]:
df_reduced_5 = df_reduced_4.loc[~df_reduced_4["X"].isin(X_dupes_2553977)]
df_reduced_5[STATS_COLS].nunique()

X                 36211
CAMID             11968
Image_name        36211
md5               36211
record_number        29
Taxonomic_Name      366
species             246
subspecies          155
genus                94
Cross_Type           30
View                  7
Locality            644
Sex                   3
Dataset               7
file_type             3
dtype: int64

4 entries were removed, reducing our number of unique `Image_name`s by 3 (one of the duplicated images had all its metadata duplicated), and everything else has remained consistent. Now the number of unique image names and entries matches the number of unique images. We have a total of 36,211 images, and we will save this reduced CSV as our new master file.

## Save Reduced Master File of Unique Images

Don't include last column indicating duplicate MD5s.

In [19]:
df_reduced_5[list(df_reduced_5.columns)[:-1]].to_csv("../Jiggins_Zenodo_Img_Master.csv", index = False)

# Generate New Master Heliconius and Dorsal Subsets

## Read in New Master File

First check on our stats noted in the README.

In [2]:
master = pd.read_csv("../Jiggins_Zenodo_Img_Master.csv", low_memory = False)
master.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 36211 entries, 0 to 36210
Data columns (total 31 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   CAMID             36211 non-null  object
 1   X                 36211 non-null  int64 
 2   Image_name        36211 non-null  object
 3   View              35432 non-null  object
 4   zenodo_name       36211 non-null  object
 5   zenodo_link       36211 non-null  object
 6   Sequence          35279 non-null  object
 7   Taxonomic_Name    36211 non-null  object
 8   Locality          23127 non-null  object
 9   Sample_accession  3647 non-null   object
 10  Collected_by      3043 non-null   object
 11  Other_ID          11329 non-null  object
 12  Date              23040 non-null  object
 13  Dataset           29114 non-null  object
 14  Store             27813 non-null  object
 15  Brood             13847 non-null  object
 16  Death_Date        269 non-null    object
 17  Cross_Type  

### Taxonomic Labeling Check

As noted above, there are instances of `<Genus> sp.` in the `Taxonomic_Name` column. These get reproduced in the `species` column as well. We also have at least one instance of just `Heliconius`, and an instance of `Unknown` was observed outside this process. To ensure the taxonomic information is indeed clear, we will print and check all 246 unique species listed in the dataset.

In [3]:
pd.Series(master.species.unique()).to_csv("../metadata/Unique_species_labels.txt", index = False)

In [4]:
species_list = list(master.species.unique())

sp_list = []
one_word_list = []
hybrid_label = []
for species in species_list:
    if "sp." in species:
        sp_list.append(species)
    if len(species.split(" ")) == 1:
        one_word_list.append(species)
    if "hybrid" in species.lower():
        hybrid_label.append(species)

print(f"We have {len(sp_list)} 'species' designations really labeled only to genus, {len(one_word_list)} species designations that may not be labeled at the species level, and {len(hybrid_label)} with 'hybrid' in the name.")

We have 24 'species' designations really labeled only to genus, 5 species designations that may not be labeled at the species level, and 1 with 'hybrid' in the name.


In [5]:
one_word_list

['Pteronymia', 'Unknown', 'Ithomiinae', 'Stratiomyidae', 'Heliconius']

In [6]:
hybrid_label

['Heliconius hybrid']

This matches my manual check:

Non-standard labels found:

- 'Heliconius hybrid'
- "sp.":
    >'Heliconius sp.', 'Melinaea sp.', 'Oleria sp.', 'Ithomia sp.', 'Godyris sp.', 'Hypothyris sp.', 'Pteronymia sp.', 'Greta sp.', 'Dircenna sp.', 'Actinote sp.', 'Eresia sp.', 'Eueides sp.', 'Pteronymia sp.nov.', 'Patricia sp.', 'Hyalyris sp.', 'Olyras sp.', 'Mechanitis sp.', 'Euides sp.', 'Taygetis sp.', 'Euselasia sp.', 'Eunica sp.', 'Ascia sp.', 'Euptychia sp.', 'Megaleas sp.'
- One name: 'Heliconius', 'Stratiomyidae', 'Ithomiinae', 'Pteronymia', + 'Unknown'.  
    - This is becuase `species` was just a split at `ssp.` and take the first element of that list, hence the duplication of single names.

### Taxonomic Labeling Fix:
- We'll adjust the genera to be `<Genus> sp.` to be consistent. Then to avoid any labeled only to the genus level, one must simply exclude those with `sp.` in the species name. 
- The `Heliconius hybrid` should be labeled as a hybrid, but have null `subspecies` value, so that should be avoidable or useable as well. 
- We will remove the `Unknown` values as their CAMIDs don't appear elsewhere so the taxonomic information is non-reconcilable. 
- Christopher confirmed that `Ithomiinae` and `Pteronymia` are genera in the family `nymphalidae`, like `Heliconius`, but `Stratiomyidae` is a "Soldier Fly" (Google, Christopher did not recognize it as a butterfly), clearly not a butterfly from the images. This label is present in [record 5561246](https://zenodo.org/records/5561246), attached to `CAMID: CAM036326`, which does not appear elsewhere in our dataset (see check below). Looking at the record, it is labeled as `BSF blue wings` in the CSV, and the images are clearly of a butterfly's wings. We have concluded it is a mislabeling and will drop it for now.

In [7]:
cams_unknown = list(master.loc[master["species"] == "Unknown", "CAMID"])
print(f"There are {len(cams_unknown)} entries with the taxonomic label 'Unknown', and {master.loc[master['CAMID'].isin(cams_unknown)].shape[0]} entries of that/those CAMID(s).")
master.loc[master["CAMID"].isin(cams_unknown), "zenodo_link"].value_counts()

There are 18 entries with the taxonomic label 'Unknown', and 18 entries of that/those CAMID(s).


zenodo_link
https://zenodo.org/record/5561246    12
https://zenodo.org/record/4291095     4
https://zenodo.org/record/2702457     2
Name: count, dtype: int64

In [8]:
cams_stratiomyidae = list(master.loc[master["species"] == "Stratiomyidae", "CAMID"])
print(f"There are {len(cams_stratiomyidae)} entries with the taxonomic label 'Stratiomyidae', and {master.loc[master['CAMID'].isin(cams_stratiomyidae)].shape[0]} entries of that/those CAMID(s).")
master.loc[master["species"] == "Stratiomyidae"]

There are 4 entries with the taxonomic label 'Stratiomyidae', and 4 entries of that/those CAMID(s).


CAMID      X       Image_name     View   zenodo_name  \
21877  CAM036326  41866  CAM036326_d.CR2   dorsal  Filelist.csv   
21878  CAM036326  41867  CAM036326_d.JPG   dorsal  Filelist.csv   
21879  CAM036326  41868  CAM036326_v.CR2  ventral  Filelist.csv   
21880  CAM036326  41869  CAM036326_v.JPG  ventral  Filelist.csv   

                             zenodo_link Sequence Taxonomic_Name  \
21877  https://zenodo.org/record/5561246   36,326  Stratiomyidae   
21878  https://zenodo.org/record/5561246   36,326  Stratiomyidae   
21879  https://zenodo.org/record/5561246   36,326  Stratiomyidae   
21880  https://zenodo.org/record/5561246   36,326  Stratiomyidae   

                           Locality Sample_accession  ... file_type  \
21877  Reserva Serra Bonita - BSF02              NaN  ...       raw   
21878  Reserva Serra Bonita - BSF02              NaN  ...       jpg   
21879  Reserva Serra Bonita - BSF02              NaN  ...       raw   
21880  Reserva Serra Bonita - BSF02              NaN  ...       jpg   

      record_number        species subspecies          genus  \
21877       5561246  Stratiomyidae        NaN  Stratiomyidae   
21878       5561246  Stratiomyidae        NaN  Stratiomyidae   
21879       5561246  Stratiomyidae        NaN  Stratiomyidae   
21880       5561246  Stratiomyidae        NaN  Stratiomyidae   

                                                file_url hybrid_stat  \
21877  https://zenodo.org/record/5561246/files/CAM036...         NaN   
21878  https://zenodo.org/record/5561246/files/CAM036...         NaN   
21879  https://zenodo.org/record/5561246/files/CAM036...         NaN   
21880  https://zenodo.org/record/5561246/files/CAM036...         NaN   

                    filename                                    filepath  \
21877  41866_CAM036326_d.CR2  images/Stratiomyidae/41866_CAM036326_d.CR2   
21878  41867_CAM036326_d.JPG  images/Stratiomyidae/41867_CAM036326_d.JPG   
21879  41868_CAM036326_v.CR2  images/Stratiomyidae/41868_CAM036326_v.CR2   
21880  41869_CAM036326_v.JPG  images/Stratiomyidae/41869_CAM036326_v.JPG   

                                    md5  
21877  4d823bf9308f967d8c1b2ea9325dac1d  
21878  23d2d33583c31c83b3e36563418204b8  
21879  d4a628aa306aa7deafa93d2b913ba4de  
21880  0a8ed38b8ad9755831bb796febaa624e  

[4 rows x 31 columns]

In [9]:
missing_label_cams = cams_unknown + cams_stratiomyidae
master.loc[master["CAMID"].isin(missing_label_cams)].to_csv("../metadata/Missing_taxa_download.csv")

In [10]:
# Drop Unknown
master = master.loc[master["species"] != "Unknown"]
master.shape[0] # should now be 36,193

36193

In [11]:
# Drop Stratiomyidae
master = master.loc[master["species"] != "Stratiomyidae"]
master.shape[0] # should now be 36,189

36189

In [12]:
# Rename 'Pteronymia', 'Ithomiinae', and 'Heliconius' as '<Genus> sp.' for consistency
rename_sp = ['Pteronymia', 'Ithomiinae', 'Heliconius']

for species in rename_sp:
    master.loc[master["species"] == species, "Taxonomic_Name"] = species + " sp."
    master.loc[master["species"] == species, "species"] = species + " sp."

In [13]:
# Check, sp_list should now be 25, as Heliconius sp. and 'Pteronymia sp.' were already on there, and our one_word_list should now be zero
species_list = list(master.species.unique())

sp_list = []
one_word_list = []
for species in species_list:
    if "sp." in species:
        sp_list.append(species)
    if len(species.split(" ")) == 1:
        one_word_list.append(species)

print(f"We have {len(sp_list)} 'species' designations really labeled only to genus, {len(one_word_list)} species designations that may not be labeled at the species level.")

We have 25 'species' designations really labeled only to genus, 0 species designations that may not be labeled at the species level.


### Stats Checks & Save

We'll now save our updated master file, then check all our stats to update the Dataset Card appropriately before regenerating our other subsets.

In [14]:
master.to_csv("../Jiggins_Zenodo_Img_Master.csv", index = False)

In [15]:
master.info()

<class 'pandas.core.frame.DataFrame'>
Index: 36189 entries, 0 to 36210
Data columns (total 31 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   CAMID             36189 non-null  object
 1   X                 36189 non-null  int64 
 2   Image_name        36189 non-null  object
 3   View              35410 non-null  object
 4   zenodo_name       36189 non-null  object
 5   zenodo_link       36189 non-null  object
 6   Sequence          35257 non-null  object
 7   Taxonomic_Name    36189 non-null  object
 8   Locality          23105 non-null  object
 9   Sample_accession  3647 non-null   object
 10  Collected_by      3043 non-null   object
 11  Other_ID          11325 non-null  object
 12  Date              23022 non-null  object
 13  Dataset           29112 non-null  object
 14  Store             27807 non-null  object
 15  Brood             13847 non-null  object
 16  Death_Date        269 non-null    object
 17  Cross_Type       

In [16]:
master.nunique()

CAMID               11962
X                   36189
Image_name          36189
View                    7
zenodo_name            31
zenodo_link            29
Sequence            10876
Taxonomic_Name        362
Locality              643
Sample_accession     1559
Collected_by           12
Other_ID             3080
Date                  804
Dataset                 7
Store                 137
Brood                 224
Death_Date             79
Cross_Type             30
Stage                   1
Sex                     3
Unit_Type               4
file_type               3
record_number          29
species               242
subspecies            155
genus                  92
file_url            36189
hybrid_stat             2
filename            36189
filepath            36189
md5                 36189
dtype: int64

Note that a total of 4 "unique" Taxonomic Names and species were removed above: "Unknown", "Heliconius", "Pteronymia", "Ithomiinae", and "Stratiomyidae" were removed and "Ithomiinae sp." was added. This process also resulted in the removal of 2 "unique" genera ("Unknown" and "Stratiomyidae").

No records were removed.

In [17]:
master.loc[master.Stage.notna()]

CAMID      X                       Image_name     View  \
13300  CAM013566  26040  13566_H_m_thelxiopeia_V.JPG.jpg  ventral   
13301  CAM013566  26039  13566_H_m_thelxiopeia_D.JPG.jpg   dorsal   
13302  CAM013715  26041      13715_H_m_meriana_D.JPG.jpg   dorsal   
13303  CAM013715  26042      13715_H_m_meriana_V.JPG.jpg  ventral   
13304  CAM013819  26044      13819_H_m_meriana_V.JPG.jpg  ventral   
13305  CAM013819  26043      13819_H_m_meriana_D.JPG.jpg   dorsal   

                                          zenodo_name  \
13300  Heliconius_wing_old_photos_2001_2019_part3.csv   
13301  Heliconius_wing_old_photos_2001_2019_part3.csv   
13302  Heliconius_wing_old_photos_2001_2019_part3.csv   
13303  Heliconius_wing_old_photos_2001_2019_part3.csv   
13304  Heliconius_wing_old_photos_2001_2019_part3.csv   
13305  Heliconius_wing_old_photos_2001_2019_part3.csv   

                             zenodo_link Sequence  \
13300  https://zenodo.org/record/2553977   13,566   
13301  https://zenodo.org/record/2553977   13,566   
13302  https://zenodo.org/record/2553977   13,715   
13303  https://zenodo.org/record/2553977   13,715   
13304  https://zenodo.org/record/2553977   13,819   
13305  https://zenodo.org/record/2553977   13,819   

                              Taxonomic_Name  \
13300  Heliconius melpomene ssp. thelxiopeia   
13301  Heliconius melpomene ssp. thelxiopeia   
13302      Heliconius melpomene ssp. meriana   
13303      Heliconius melpomene ssp. meriana   
13304      Heliconius melpomene ssp. meriana   
13305      Heliconius melpomene ssp. meriana   

                                Locality Sample_accession  ... file_type  \
13300                        Maripasoula        ERS977708  ...       jpg   
13301                        Maripasoula        ERS977708  ...       jpg   
13302  N. Wakapou, Maripausala FR GUIANA        ERS977704  ...       jpg   
13303  N. Wakapou, Maripausala FR GUIANA        ERS977704  ...       jpg   
13304  N. Wakapou, Maripausala FR GUIANA        ERS977703  ...       jpg   
13305  N. Wakapou, Maripausala FR GUIANA        ERS977703  ...       jpg   

      record_number               species   subspecies       genus  \
13300       2553977  Heliconius melpomene  thelxiopeia  Heliconius   
13301       2553977  Heliconius melpomene  thelxiopeia  Heliconius   
13302       2553977  Heliconius melpomene      meriana  Heliconius   
13303       2553977  Heliconius melpomene      meriana  Heliconius   
13304       2553977  Heliconius melpomene      meriana  Heliconius   
13305       2553977  Heliconius melpomene      meriana  Heliconius   

                                                file_url hybrid_stat  \
13300  https://zenodo.org/record/2553977/files/13566_...  non-hybrid   
13301  https://zenodo.org/record/2553977/files/13566_...  non-hybrid   
13302  https://zenodo.org/record/2553977/files/13715_...  non-hybrid   
13303  https://zenodo.org/record/2553977/files/13715_...  non-hybrid   
13304  https://zenodo.org/record/2553977/files/13819_...  non-hybrid   
13305  https://zenodo.org/record/2553977/files/13819_...  non-hybrid   

                                    filename  \
13300  26040_13566_H_m_thelxiopeia_V.JPG.jpg   
13301  26039_13566_H_m_thelxiopeia_D.JPG.jpg   
13302      26041_13715_H_m_meriana_D.JPG.jpg   
13303      26042_13715_H_m_meriana_V.JPG.jpg   
13304      26044_13819_H_m_meriana_V.JPG.jpg   
13305      26043_13819_H_m_meriana_D.JPG.jpg   

                                                filepath  \
13300  images/Heliconius melpomene ssp. thelxiopeia/2...   
13301  images/Heliconius melpomene ssp. thelxiopeia/2...   
13302  images/Heliconius melpomene ssp. meriana/26041...   
13303  images/Heliconius melpomene ssp. meriana/26042...   
13304  images/Heliconius melpomene ssp. meriana/26044...   
13305  images/Heliconius melpomene ssp. meriana/26043...   

                                    md5  
13300  b5ed68f937132cbbb04a81d550c9f17e  
13301  cb107e2d6a2c3c84b68bbf4e3cfa7af7  
13302

In [18]:
master.loc[master.Cross_Type.notna()].nunique()

CAMID                820
X                   4447
Image_name          4447
View                   2
zenodo_name            4
zenodo_link            4
Sequence             820
Taxonomic_Name         8
Locality               0
Sample_accession       0
Collected_by           0
Other_ID               0
Date                 160
Dataset                1
Store                 10
Brood                 49
Death_Date             0
Cross_Type            30
Stage                  0
Sex                    2
Unit_Type              1
file_type              2
record_number          4
species                2
subspecies            21
genus                  1
file_url            4447
hybrid_stat            2
filename            4447
filepath            4447
md5                 4447
dtype: int64

In [19]:
master.View.value_counts()

View
dorsal                17224
ventral               17156
hindwing dorsal         254
hindwing ventral        254
forewing dorsal         252
forewing ventral        252
dorsal and ventral       18
Name: count, dtype: int64

In [20]:
master.Sex.value_counts()

Sex
Male       15904
Female     11323
Unknown      283
Name: count, dtype: int64

Generate master_licenses CSV file to re-run [`get_licenses.py`](https://huggingface.co/datasets/imageomics/Comparison-Subset-Jiggins/blob/main/scripts/get_licenses.py) for nicely formatted licensing info of the 29 included records.


In [24]:
master_licenses = master[["record_number", "zenodo_link"]]
master_licenses = master_licenses.loc[~master_licenses.duplicated(["record_number", "zenodo_link"], keep = "first")]
master_licenses.shape

(29, 2)

In [25]:
master_licenses.rename(columns = {"zenodo_link": "url"}, inplace = True)
master_licenses.head(2)

record_number                                url
0          4289223  https://zenodo.org/record/4289223
145        4288311  https://zenodo.org/record/4288311

In [26]:
# Save to CSV to run through get licenses script
master_licenses.to_csv("../metadata/master_licenses.csv", index = False)

## Make Heliconius Master Subset

Now make the Heliconius master CSV, and check stats to update README.

In [21]:
heliconius_master = master.loc[master.genus.str.lower() == "heliconius"].copy()
heliconius_master.nunique()

CAMID               10086
X                   29134
Image_name          29134
View                    3
zenodo_name            31
zenodo_link            29
Sequence             9008
Taxonomic_Name        131
Locality              471
Sample_accession     1559
Collected_by           12
Other_ID             1865
Date                  773
Dataset                 7
Store                 121
Brood                 224
Death_Date             79
Cross_Type             30
Stage                   1
Sex                     3
Unit_Type               4
file_type               3
record_number          29
species                36
subspecies            110
genus                   1
file_url            29134
hybrid_stat             2
filename            29134
filepath            29134
md5                 29134
dtype: int64

In [22]:
heliconius_master.View.value_counts()

View
dorsal                14202
ventral               14135
dorsal and ventral       18
Name: count, dtype: int64

### Save Heliconius Subset to CSV

In [23]:
heliconius_master.to_csv("../Jiggins_Heliconius_Master.csv", index = False)

## Make Dorsal Subset

We'll now make a CSV of all dorsal images.

In [24]:
dorsal_views = [view for view in list(master.View.dropna().unique()) if "dorsal" in view]

dorsal_master = master.loc[master["View"].isin(dorsal_views)].copy()
dorsal_master.nunique()

CAMID               11746
X                   17748
Image_name          17748
View                    4
zenodo_name            31
zenodo_link            29
Sequence            10683
Taxonomic_Name        358
Locality              640
Sample_accession     1552
Collected_by           12
Other_ID             2889
Date                  788
Dataset                 7
Store                 137
Brood                 215
Death_Date             61
Cross_Type             30
Stage                   1
Sex                     3
Unit_Type               4
file_type               3
record_number          29
species               241
subspecies            152
genus                  92
file_url            17748
hybrid_stat             2
filename            17748
filepath            17748
md5                 17748
dtype: int64

In [25]:
dorsal_master["CAM_dupe"] = dorsal_master.duplicated(["CAMID", "file_type"], keep = False)
dorsal_master.CAM_dupe.value_counts()

CAM_dupe
False    15449
True      2299
Name: count, dtype: int64

In [26]:
# Adding label for both wings alters counts, as in, some only have the double wing image
dorsal_master.loc[dorsal_master["View"].isin(["forewing dorsal", "hindwing dorsal"]), "CAM_dupe"] = "single-wing"
dorsal_master.loc[dorsal_master["View"] == "dorsal and ventral", "CAM_dupe"] = "both-wings"
dorsal_master.CAM_dupe.value_counts()

CAM_dupe
False          15431
True            1793
single-wing      506
both-wings        18
Name: count, dtype: int64

In [27]:
print(dorsal_master.loc[dorsal_master["CAM_dupe"] == True, "CAMID"].nunique())
print(dorsal_master.loc[dorsal_master["CAM_dupe"] == False, "CAMID"].nunique())
dorsal_master.loc[dorsal_master["CAM_dupe"] == True, "record_number"].nunique()

881
11446


13

In [28]:
dorsal_master.loc[dorsal_master["CAM_dupe"] == "single-wing", "file_type"].value_counts()

file_type
raw    253
jpg    253
Name: count, dtype: int64

In [29]:
dorsal_master.loc[dorsal_master["CAM_dupe"] == "both-wings", "file_type"].value_counts()

file_type
jpg    17
tif     1
Name: count, dtype: int64

In [30]:
dorsal_master.loc[dorsal_master["CAM_dupe"] == True, "file_type"].value_counts()

file_type
jpg    1775
tif      16
raw       2
Name: count, dtype: int64

In [31]:
dorsal_master.loc[dorsal_master["CAM_dupe"] == False, "file_type"].value_counts()

file_type
jpg    10700
raw     4713
tif       18
Name: count, dtype: int64

In [32]:
dorsal_master.loc[dorsal_master["file_type"] == "jpg"].duplicated(subset = "CAMID", keep = False).value_counts()

False    10717
True      2028
Name: count, dtype: int64

In [33]:
dorsal_master.loc[dorsal_master["file_type"] == "raw"].duplicated(subset = "CAMID", keep = False).value_counts()

False    4714
True      254
Name: count, dtype: int64

Generally speaking, it seems RAW images will be unique, as there is only one CAMID that gets duplicated across the raw images (2 photos of that specimen that are RAW) outside of the single wing views.

### Save Dorsal Subset to CSV

In [34]:
dorsal_master.to_csv("../Jiggins_Zenodo_dorsal_Img_Master.csv", index = False)